In [4]:
from pymongo import MongoClient
import gridfs

In [6]:
db = MongoClient().dnn
fs = gridfs.GridFS(db)

def get_run(run_id):
    return db.runs.find_one({"_id" : run_id});
    
def save_artifact(run, filename, name):
    with open(filename, 'rb') as f:
        run_id = run['_id']
        db_filename = 'artifact://{}/{}/{}'.format("runs", run_id, name)
        file_id = fs.put(f, filename=db_filename)    
        
    run["artifacts"].append({'name': name,'file_id': file_id})
    db.runs.update_one({'_id': run['_id']}, {'$set': run})
    
def download_artifacts(run):
    for a in run["artifacts"]:
        with open(a["name"], 'wb') as f:
            fs.download_to_stream(a["file_id"], f)
            
def delete_artifacts(run):
    for a in run["artifacts"]:
        fs.delete(a["file_id"])
    run["artifacts"] = []
    db.runs.update_one({'_id': run['_id']}, {'$set': run})

In [7]:
get_run(1)

{'_id': 1,
 'experiment': {'name': 'DNN Experiment',
  'base_dir': '/home/carlo/work/RobustTransfer/src',
  'sources': [['dnn.py', ObjectId('5cba1b9a921807bafbbe0c99')]],
  'dependencies': ['numpy==1.16.2',
   'sacred==0.7.4',
   'torch==1.0.1',
   'tqdm==4.29.0'],
  'repositories': [],
  'mainfile': 'dnn.py'},
 'format': 'MongoObserver-0.7.0',
 'command': 'main',
 'host': {'hostname': 'europa',
  'os': ['Linux', 'Linux-5.0.5-1-MANJARO-x86_64-with-arch-Manjaro-Linux'],
  'python_version': '3.7.3',
  'cpu': 'AMD Ryzen Threadripper 2950X 16-Core Processor',
  'gpus': {'gpus': [{'model': 'GeForce RTX 2080 Ti',
     'total_memory': 10981,
     'persistence_mode': False}],
   'driver_version': '418.43'},
  'ENV': {}},
 'start_time': datetime.datetime(2019, 4, 19, 19, 3, 54, 351000),
 'config': {'batch_size': 128,
  'dataset': 'fashion',
  'droplr': False,
  'epochs': 100,
  'exclude_class': -1,
  'load_model': '',
  'logtime': 2,
  'loss': 'nll',
  'lr': 0.001,
  'model': 'lenet',
  'no_cud